AWS GET CLI Details

In [1]:
import os
import boto3
import pandas as pd
import json
from dotenv import load_dotenv
load_dotenv()


os.environ['AWS_DEFAULT_REGION'] = os.getenv('AWS_DEFAULT_REGION')
os.environ['AWS_ACCESS_KEY_ID'] = os.getenv('AWS_ACCESS_KEY_ID')
os.environ['AWS_SECRET_ACCESS_KEY'] = os.getenv('AWS_SECRET_ACCESS_KEY')

print("REGION:", os.environ['AWS_DEFAULT_REGION'])
print("KEY ID:", os.environ['AWS_ACCESS_KEY_ID'][:4] + '…')

# Use boto3 to interact with AWS
ec2 = boto3.client('ec2')
print("Default region:", ec2.meta.region_name)
print("Regions list:", [r['RegionName'] for r in ec2.describe_regions()['Regions']])

REGION: ap-south-1
KEY ID: AKIA…
Default region: ap-south-1
Regions list: ['ap-south-1', 'eu-north-1', 'eu-west-3', 'eu-west-2', 'eu-west-1', 'ap-northeast-3', 'ap-northeast-2', 'ap-northeast-1', 'ca-central-1', 'sa-east-1', 'ap-southeast-1', 'ap-southeast-2', 'eu-central-1', 'us-east-1', 'us-east-2', 'us-west-1', 'us-west-2']


In [2]:
def get_category_definitions():
    """
    Return a dict mapping each category name to the set of
    instance‐family prefixes that belong in it.
    Edit this one place whenever AWS adds a new family.
    """
    return {
        'Accelerated Computing': {
            'P5','P4','G6E','G6','G5G','G5','G4DN','G4AD',
            'TRN2','TRN1','INF2','INF1','DL1','DL2Q','F2','VT1'
        },
        'Compute Optimized': {
            'C8G','C7G','C7GN','C7I','C7I-FLEX','C7A',
            'C6G','C6GN','C6I','C6IN','C6A','C5','C5N','C5A','C4',
            'C6GD','C5D','C7GD','C6ID','C3','C5AD','C1','C8GD'
        },
        'General Purpose': {
            'M8G','M7G','M7I','M7I-FLEX','M7A','MAC',
            'M6G','M6I','M6IN','M6A','M5','M5N','M5ZN','M5A','M4',
            'T4G','T3','T3A','T2','M5AD','M6GD','M5D','M7GD','M6ID',
            'M6IDN','A1','MAC1','M5DN','T1','M1','MAC2','M3','MAC2-M2',
            'MAC2-M2PRO','M8GD',
        },
        'HPC Optimized': {
            'HPC7G','HPC7A','HPC6ID','HPC6A'
        },
        'Memory Optimized': {
            'R8G','R7G','R7I','R7IZ','R7A',
            'R6G','R6I','R6IN','R6A',
            'R5','R5N','R5B','R5A','R4','R3',
            'U7I','U-1',
            'X8G','X2GD','X2IDN','X2IEDN','X2IEZN',
            'X1','X1E','Z1D','R5AD','R6GD','R6ID','R7GD',
            'R5D','U-12TB1','U-6TB1','U-9TB1','R6IDN','R5DN','M2',
            'U-3TB1','U-18TB1','U7I-6TB','U-24TB1','U7IN-16TB','U7I-8TB',
            'R8GD','U7IN-24TB','U7I-12TB','U7IN-32TB' 

        },
        'Storage Optimized': {
            'I8G','I7I','I7IE','I4G','IM4GN','IS4GEN',
            'I4I','I3','I3EN',
            'D3','D3EN','D2','H1','I2'
        },
        'GPU Optimized': {
            'P4D','GR6','P5EN','P5E','P3','P3DN'
        }
    }

# Cost Per Hours

In [3]:
def build_category_map(category_defs: dict[str, set[str]]) -> dict[str, str]:
    """
    Invert category_defs so that each family prefix maps to its category.
    """
    cmap: dict[str, str] = {}
    for category, prefixes in category_defs.items():
        for prefix in prefixes:
            cmap[prefix.upper()] = category
    return cmap

In [4]:
import botocore.session
def build_region_to_location_map():
    """
    Map every region code (e.g. 'eu-central-1') to its human name,
    and normalize any "Europe"→"EU" so it matches Pricing API.
    """
    session    = botocore.session.get_session()
    parts      = session.get_data('partitions')['partitions']
    region_map: dict[str, str] = {}
    for part in parts:
        for code, info in part.get('regions', {}).items():
            desc = info.get('description', '')
            # Pricing API uses "EU (...)" not "Europe (...)"
            desc = desc.replace('Europe', 'EU')
            region_map[code] = desc
    return region_map

In [5]:
def get_all_on_demand_prices(
    operating_system: str = "Linux",
    tenancy: str         = "Shared",
    pre_installed_sw: str= "NA",
    capacitystatus: str  = "Used",
) -> dict[tuple[str,str], float]:
    """
    Paginate over the Pricing API to fetch every On-Demand price
    for EC2 (USD/hr), filtered by OS/tenancy/etc.
    Returns a dict: { (instanceType, locationKey) -> price_float }.
    We key by both the human name (e.g. "EU (Frankfurt)") and the code ("eu-central-1").
    """
    pricing   = boto3.client("pricing", region_name="us-east-1")
    paginator = pricing.get_paginator("get_products")

    filters = [
        {"Type": "TERM_MATCH", "Field": "operatingSystem", "Value": operating_system},
        {"Type": "TERM_MATCH", "Field": "preInstalledSw",   "Value": pre_installed_sw},
        {"Type": "TERM_MATCH", "Field": "tenancy",          "Value": tenancy},
        {"Type": "TERM_MATCH", "Field": "capacitystatus",   "Value": capacitystatus},
    ]

    # build mapping code↔desc so we can duplicate keys
    region_map   = build_region_to_location_map()
    desc_to_code = {desc: code for code, desc in region_map.items()}

    price_map: dict[tuple[str,str], float] = {}
    for page in paginator.paginate(
        ServiceCode="AmazonEC2",
        Filters=filters,
        FormatVersion="aws_v1",
    ):
        for price_str in page["PriceList"]:
            prod = json.loads(price_str)
            attrs = prod["product"]["attributes"]
            itype = attrs["instanceType"]
            loc   = attrs["location"]           # e.g. "EU (Frankfurt)"
            od    = next(iter(prod["terms"]["OnDemand"].values()))
            pdim  = next(iter(od["priceDimensions"].values()))

            # extract USD/hour
            per_unit = pdim["pricePerUnit"]
            if isinstance(per_unit, dict):
                # e.g. {"USD": "0.0960000000"}
                currency_key = next(iter(per_unit))
                usd = float(per_unit[currency_key])
            else:
                usd = float(per_unit)

            # store under both human name and region code (if available)
            price_map[(itype, loc)] = usd
            if loc in desc_to_code:
                price_map[(itype, desc_to_code[loc])] = usd

    return price_map

In [6]:
def collect_all_instance_types(
    operating_system: str = "Linux",
    tenancy: str         = "Shared",
    pre_installed_sw: str= "NA",
    capacitystatus: str  = "Used",
):
    """
    Describe every instance type in every region, merge in the On-Demand
    cost (USD/hr) by trying both the code (eu-…) and human name ("EU (…)").
    """
    ec2     = boto3.client('ec2')
    regions = [r['RegionName'] for r in ec2.describe_regions()['Regions']]

    region_map   = build_region_to_location_map()
    category_map = build_category_map(get_category_definitions())
    price_map    = get_all_on_demand_prices(
        operating_system, tenancy, pre_installed_sw, capacitystatus
    )

    rows: list[dict] = []
    for region in regions:
        client        = boto3.client("ec2", region_name=region)
        paginator     = client.get_paginator("describe_instance_types")
        location_name = region_map.get(region, region)

        for page in paginator.paginate():
            for it in page["InstanceTypes"]:
                itype      = it["InstanceType"]
                family     = itype.split(".", 1)[0].upper()
                category   = category_map.get(family, "Other")
                mem_mib    = it["MemoryInfo"]["SizeInMiB"]
                ram_gib    = round(mem_mib / 1024, 2)
                net_perf   = it.get("NetworkInfo", {}).get("NetworkPerformance")
                # try code first, then human name
                cost_hr    = price_map.get((itype, region),
                             price_map.get((itype, location_name)))

                rows.append({
                    "Region":                   region,
                    "Instance Type":            itype,
                    "Instance Family":          category,
                    "vCPUs":                    it["VCpuInfo"]["DefaultVCpus"],
                    "RAM (GiB)":                ram_gib,
                    "Memory MiB":               mem_mib,
                    "Cost Per Hour":            cost_hr,
                    "Storage Info":             it.get("InstanceStorageInfo"),
                    "Network Performance":      net_perf,
                    "Accelerators":             it.get("GpuInfo") or it.get("FpgaInfo"),
                })

    return pd.DataFrame(rows)

In [7]:
df_types = collect_all_instance_types(
        operating_system="Linux",
        tenancy="Shared",
        pre_installed_sw="NA",
        capacitystatus="Used"
    )

In [8]:
print(df_types.columns)
df_types.head()
print(df_types.to_string())

Index(['Region', 'Instance Type', 'Instance Family', 'vCPUs', 'RAM (GiB)',
       'Memory MiB', 'Cost Per Hour', 'Storage Info', 'Network Performance',
       'Accelerators'],
      dtype='object')
               Region        Instance Type        Instance Family  vCPUs  RAM (GiB)  Memory MiB  Cost Per Hour                                                                                                                                           Storage Info  Network Performance                                                                                                                                                   Accelerators
0          ap-south-1    m7i-flex.12xlarge        General Purpose     48     192.00      196608        2.41800                                                                                                                                                   None  Up to 18.75 Gigabit                                                                              

In [9]:
print("Number of rows:", df_types.shape[0])
print("Number of columns:", df_types.shape[1])
print(df_types.count())

Number of rows: 10972
Number of columns: 10
Region                 10972
Instance Type          10972
Instance Family        10972
vCPUs                  10972
RAM (GiB)              10972
Memory MiB             10972
Cost Per Hour          10936
Storage Info            4571
Network Performance    10972
Accelerators             587
dtype: int64


In [10]:
output_path = "Final_AWS_Test_Data.csv"
df_types.to_csv(output_path, index=False)

print(f"Exported {len(df_types)} rows to {output_path}")

Exported 10972 rows to Final_AWS_Test_Data.csv
